In [1]:
import json

import gravis as gv
import networkx as nx

from nomad_utility_workflows.utils.workflows import (
    NodeAttributes,
    NodeAttributesUniverse,
    build_nomad_workflow,
    nodes_to_graph,
)

In [2]:
with open('PIDs.json') as f:
    pids_dict = json.load(f)
entry_ids = pids_dict.get('entry_ids')
upload_ids = pids_dict.get('upload_ids')
print(entry_ids)
print(upload_ids)

{'md-workflow': 'J3Vkhz2NAtSw4-KTnbHqUyPhhY3g', 'DFT': ['d2ZJkTjL4LoxdFAVS8YT_jlZdzhm', 'zeiiGOoZL0dikRgYSvzuZZ3xPv9m', '8x9j0tEtx6LeGVEv7ByWD3k5VK1F'], 'setup-workflow': '8EcTSRbvb8PiYaG_TwqAgOYiE8J7', 'parameters': 'ujuIHCdj7StVCxbvYP7NjMvG4v22', 'analysis': 'zv4Q_jnvhsGry4oEyj5AC2qD103H'}
{'md-workflow': '7Ncu4YyXTTyTSfg0qpiziQ', 'DFT': ['JHsC4UFnRtCB9dQYR1BO6A', 'exkqL5J8Q62ldMHbuE5tcQ', '0wUg7_GuSLiG3U1LcNlr2A'], 'setup-workflow': 'ME2oYBdiQUW4CGcG0YsGuw', 'analysis': 'yyqHpBFOSxqhrNALIJswSw'}


In [3]:
node_attributes = {
    0: NodeAttributes(
        name='Workflow Parameters',
        type='input',
        path_info={
            'entry_id': entry_ids.get('parameters'),
            'upload_id': upload_ids.get('setup-workflow'),
            'mainfile_path': 'workflow_parameters.archive.yaml',
            'archive_path': 'data',
        },
    ),
    1: NodeAttributes(
        name='MD Setup',
        type='workflow',
        path_info={
            'entry_id': entry_ids.get('setup-workflow'),
            'upload_id': upload_ids.get('setup-workflow'),
            'mainfile_path': 'setup_workflow.archive.yaml',
        },
        in_edge_nodes=[0],
    ),
    2: NodeAttributes(
        name='MD Equilibration',
        type='workflow',
        path_info={
            'entry_id': entry_ids.get('md-workflow'),
            'upload_id': upload_ids.get('md-workflow'),
            'mainfile_path': 'workflow.archive.yaml',
        },
        in_edge_nodes=[1],
    ),
    3: NodeAttributes(
        name='DFT-1',
        type='workflow',
        entry_type='simulation',
        path_info={
            'entry_id': entry_ids.get('DFT')[0],
            'upload_id': upload_ids.get('DFT')[0],
            'mainfile_path': 'aims.out'
            },
        in_edge_nodes=[2],
        out_edge_nodes=[6],
    ),
    4: NodeAttributes(
        name='DFT-2',
        type='task',
        entry_type='simulation',
        path_info={
            'entry_id': entry_ids.get('DFT')[1],
            'upload_id': upload_ids.get('DFT')[1],
            'mainfile_path': 'aims.out'
            },
        in_edge_nodes=[2],
        out_edge_nodes=[6],
    ),
    5: NodeAttributes(
        name='DFT-3',
        type='task',
        entry_type='simulation',
        path_info={
            'entry_id': entry_ids.get('DFT')[2],
            'upload_id': upload_ids.get('DFT')[2],
            'mainfile_path': 'aims.out'
            },
        in_edge_nodes=[2],
        out_edge_nodes=[6],
    ),
    6: NodeAttributes(
        name='Vibrational Analysis',
        type='output',
        path_info={
            'entry_id': entry_ids.get('analysis'),
            'upload_id': upload_ids.get('analysis'),
            'mainfile_path': 'vibrational_analysis.archive.yaml',
            'archive_path': 'data',
        },
    ),
}

In [4]:
node_attributes

{0: NodeAttributes(name='Workflow Parameters', type='input', entry_type=None, path_info={'upload_id': 'ME2oYBdiQUW4CGcG0YsGuw', 'entry_id': 'ujuIHCdj7StVCxbvYP7NjMvG4v22', 'mainfile_path': 'workflow_parameters.archive.yaml', 'archive_path': 'data'}, inputs=[], outputs=[], in_edge_nodes=[], out_edge_nodes=[]),
 1: NodeAttributes(name='MD Setup', type='workflow', entry_type=None, path_info={'upload_id': 'ME2oYBdiQUW4CGcG0YsGuw', 'entry_id': '8EcTSRbvb8PiYaG_TwqAgOYiE8J7', 'mainfile_path': 'setup_workflow.archive.yaml', 'archive_path': 'workflow2'}, inputs=[], outputs=[], in_edge_nodes=[0], out_edge_nodes=[]),
 2: NodeAttributes(name='MD Equilibration', type='workflow', entry_type=None, path_info={'upload_id': '7Ncu4YyXTTyTSfg0qpiziQ', 'entry_id': 'J3Vkhz2NAtSw4-KTnbHqUyPhhY3g', 'mainfile_path': 'workflow.archive.yaml', 'archive_path': 'workflow2'}, inputs=[], outputs=[], in_edge_nodes=[1], out_edge_nodes=[]),
 3: NodeAttributes(name='DFT-1', type='workflow', entry_type='simulation', path

In [5]:
node_attributes_universe = NodeAttributesUniverse(nodes=node_attributes)

In [6]:
workflow_graph_input = nodes_to_graph(node_attributes_universe)

In [7]:
gv.d3(
    workflow_graph_input,
    node_label_data_source='name',
    edge_label_data_source='name',
    zoom_factor=1.5,
    node_hover_tooltip=True,
)

In [8]:
for node_key, node_attributes in workflow_graph_input.nodes(data=True):
    if 'in_edge_nodes' in node_attributes:
        del node_attributes['in_edge_nodes']
    if 'out_edge_nodes' in node_attributes:
        del node_attributes['out_edge_nodes']

for node_key, node_attributes in list(workflow_graph_input.nodes(data=True)):
    print(node_key, node_attributes)

0 {'name': 'Workflow Parameters', 'type': 'input', 'entry_type': None, 'path_info': {'upload_id': 'ME2oYBdiQUW4CGcG0YsGuw', 'entry_id': 'ujuIHCdj7StVCxbvYP7NjMvG4v22', 'mainfile_path': 'workflow_parameters.archive.yaml', 'archive_path': 'data'}}
1 {'name': 'MD Setup', 'type': 'workflow', 'entry_type': None, 'path_info': {'upload_id': 'ME2oYBdiQUW4CGcG0YsGuw', 'entry_id': '8EcTSRbvb8PiYaG_TwqAgOYiE8J7', 'mainfile_path': 'setup_workflow.archive.yaml', 'archive_path': 'workflow2'}}
2 {'name': 'MD Equilibration', 'type': 'workflow', 'entry_type': None, 'path_info': {'upload_id': '7Ncu4YyXTTyTSfg0qpiziQ', 'entry_id': 'J3Vkhz2NAtSw4-KTnbHqUyPhhY3g', 'mainfile_path': 'workflow.archive.yaml', 'archive_path': 'workflow2'}}
3 {'name': 'DFT-1', 'type': 'workflow', 'entry_type': 'simulation', 'path_info': {'upload_id': 'JHsC4UFnRtCB9dQYR1BO6A', 'entry_id': 'd2ZJkTjL4LoxdFAVS8YT_jlZdzhm', 'mainfile_path': 'aims.out', 'archive_path': 'workflow2'}}
4 {'name': 'DFT-2', 'type': 'task', 'entry_type': 's

In [9]:
for edge_1, edge_2, edge_attributes in workflow_graph_input.edges(data=True):
    print(edge_1, edge_2, edge_attributes)

0 1 {}
1 2 {}
2 3 {}
2 4 {}
2 5 {}
3 6 {}
4 6 {}
5 6 {}


In [ ]:
workflow_metadata = {
    'destination_filename': './project_workflow_upload-and-entry-ids.archive.yaml',
    'workflow_name': 'NOMAD Tutorial Workflows Project',
}

workflow_graph_output = build_nomad_workflow(
    workflow_metadata=workflow_metadata,
    workflow_graph=nx.DiGraph(workflow_graph_input),
    write_to_yaml=True,
)

In [11]:
gv.d3(
    workflow_graph_output,
    node_label_data_source='name',
    edge_label_data_source='name',
    zoom_factor=1.5,
    node_hover_tooltip=True,
)